![IBGE LOGO](https://s3-sa-east-1.amazonaws.com/arrematearte-farm/cristinagoston/lot_photos/11920/e2b04faba30f14f269a12c88c1dffc839e637495_ml.jpg)



# CAMADA BRONZE

In [0]:
from delta.tables import *
from pyspark.sql.types import *
from pyspark.sql.functions import col
import pytz
from pyspark.sql.functions import lit
from pyspark.sql import Window
from pyspark.sql.functions import *
from datetime import datetime

import requests
import json

In [0]:
try:
  time_file = datetime.now(pytz.timezone('America/Sao_Paulo')).strftime('%Y%m%d_%H%M%S')
  # DeltaTable.isDeltaTable(spark, bronze_delta_path)

  #### Nome  e caminho onde será feita a escrita da da tabela Delta  ##########
  db = 'bronze.'
  table = 'ibge_news'
  delta_table = f'{db}{table}'
  bronze_delta_path = 'dbfs:/mnt/bronze/'

  ### Sistema de origem ####
  source_system_path = 'dbfs:/mnt/raw_3/'

  ### caminho para gravação do histórico ###
  historic_path = 'dbfs:/mnt/historic/bronze/'
  
  print("##----------------------------##")
  print(f"Data e Horário de execusão             ===> {time_file} \n")
  print(f"Tabela bronze a ser criada             ===>  {delta_table}")
  print(f"Caminho da tabela Bronze a ser criada  ===> {bronze_delta_path} \n")
  print("##----------------------------##")
  print(f"Sistema de origem                      ===> {source_system_path}")
  print(f"Caminho para gravação do histórico     ===> {historic_path}")
except Exception as e:
  print(e)

##----------------------------##
Data e Horário de execusão             ===> 20241013_085336 

Tabela bronze a ser criada             ===>  bronze.ibge_news
Caminho da tabela Bronze a ser criada  ===> dbfs:/mnt/bronze/ 

##----------------------------##
Sistema de origem                      ===> dbfs:/mnt/raw_3/
Caminho para gravação do histórico     ===> dbfs:/mnt/historic/bronze/


### Listando arquivos camada RAW

### Separando Arquivos de 10 em 10

### Criando Classe de Ingestao na Bronze

In [0]:
class BronzeIngestion:

  def __init__(self,db,table,bronze_delta_path,source_system_path,historic_path):
    self.db                 = db
    self.table              = table
    self.delta_table        = f"{self.db}.{self.table}"
    self.bronze_delta_path  = bronze_delta_path
    self.source_system_path = source_system_path
    self.historic_path      = historic_path

  ### Listando arquivos camada RAW   ####
  def list_all_files(self):
    try:
      ### self.source_system_path => sistema de origem   ####
      all_files = []
      for files in dbutils.fs.ls(self.source_system_path):
        all_files.append([files.path,files.path.split("_")[-1].replace("/","")])
      all_files.sort(key = lambda pos:pos[1])
      # print(all_files)
      return [all_files[i][0] for i in range(0,len(all_files))]

    except Exception as error:
      print(f"{error}") 


  
  def separate_files(self):
    try:
      ### Separando arquivos a cada 10 items ou a quantidade que for..
      ### caso seja menor do que 10
      all_files = self.list_all_files()
      return  [ all_files[i:i+10] for i in range(0,len(all_files),10)]
    
    except Exception as error:
      print(f"{error}") 
  
  ### Salvando Dados na camada Bronze ###
  def save_files_delta(self):
    try:
      print(" Inicinado método list_all_files().... \n Inicinado método list_all_files() .... \n Inicinado método save_files_delta() ....\n")
      files_to_record = self.separate_files()
      for files in files_to_record:
        # print(files,len(files),"\n")
        df =spark.read.json(files)
        #### Adicionando data de ingestao ####
        df = df.withColumn('DTPROC',lit(datetime.now(pytz.timezone('America/Sao_Paulo')).strftime('%Y%m%d_%H%M%S')))
        print(f" Salvando dados da API no caminho ===> {self.bronze_delta_path}  com o nome ===>  {self.delta_table} ")
        df.write.mode('append').format('delta').save(self.bronze_delta_path)
      print("\n Dados salvos em formato delta. \n")
    except Exception as error:
      print(f"{error}")

  ##### Copiando arquivos para Historico  ####
  def copy_to_historic(self):
    try:
      print(f"\n Copiando arquivos de ==> {self.source_system_path} para ==>  {self.historic_path} \n ")
      dbutils.fs.cp(self.source_system_path,self.historic_path,recurse = True)
      print(" Copia realizada com sucesso.\n")
    except Exception as error:
      print(f"{error}")
  
  
  ### Criando tabela no hive_metastore (catalogo Databricks)  ####
  def create_delta_table_hive(self):
    try:
      sql = f""" CREATE DATABASE IF NOT EXISTS {self.db} """
      spark.sql(sql)
      print(sql,"\n")

      sql_drop = f""" DROP TABLE IF EXISTS {self.delta_table}  """
      spark.sql(sql_drop)
      print(sql_drop,"\n") 

      sql_table = f""" CREATE TABLE IF NOT EXISTS {self.delta_table} USING DELTA LOCATION '{self.bronze_delta_path}' """
      spark.sql(sql_table)
      print(sql_table)

    except Exception as error:
      print(f"{error}")

  

  #### Executando  ####
  def bronze_run(self):
    print("Inicio do processo de ingestão na bronze... \n")
    # self.list_all_files()
    # self.separate_files()
    self.save_files_delta()
    self.copy_to_historic()
    self.create_delta_table_hive()
    print("Processo finalizado!..")

In [0]:
bronze = BronzeIngestion('bronze','ibge_news','dbfs:/mnt/bronze/','dbfs:/mnt/raw_3/','dbfs:/mnt/historic/bronze/')
bronze.bronze_run()

Inicio do processo de ingestão na bronze... 

 Inicinado método list_all_files().... 
 Inicinado método list_all_files() .... 
 Inicinado método save_files_delta() ....

 Salvando dados da API no caminho ===> dbfs:/mnt/bronze/  com o nome ===>  bronze.ibge_news 
 Salvando dados da API no caminho ===> dbfs:/mnt/bronze/  com o nome ===>  bronze.ibge_news 
 Salvando dados da API no caminho ===> dbfs:/mnt/bronze/  com o nome ===>  bronze.ibge_news 

 Dados salvos em formato delta. 


 Copiando arquivos de ==> dbfs:/mnt/raw_3/ para ==>  dbfs:/mnt/historic/bronze/ 
 
 Copia realizada com sucesso.

 CREATE DATABASE IF NOT EXISTS bronze  

 DROP TABLE IF EXISTS bronze.ibge_news   

 CREATE TABLE IF NOT EXISTS bronze.ibge_news USING DELTA LOCATION 'dbfs:/mnt/bronze/' 
Processo finalizado!..


In [0]:
%sql
-- select count(*) from delta.`dbfs:/mnt/bronze/`
select * from bronze.ibge_news

PAGE data_publicacao destaque editorias id imagens introducao link produto_id produtos produtos_relacionados tipo titulo DTPROC 101 - to - 110 - 20241012_093551 27/06/2018 10:00:00 true economicas 21561 {"image_intro":"","float_intro":"","image_intro_alt":"","image_intro_caption":"","image_fulltext":"images\/agenciadenoticias\/releases_2017\/CadastroAgencia2_portal_agencia_pesquisas_876-x-485px.jpg","float_fulltext":"","image_fulltext_alt":"#PraCegoVer Vista a\u00e9rea de cont\u00e2ineres no Porto","image_fulltext_caption":""} Em 2016, as 5,1 milhões de empresas e outras organizações ativas no país tinham 5,5 milhões de unidades locais e ocuparam 51,4 milhões de pessoas, das quais 44,5 milhões assalariadas, que receberam R$ 1,6 trilhão em salários e outras remunerações. O... http://agenciadenoticias.ibge.gov.br/agencia-sala-de-imprensa/2013-agencia-de-noticias/releases/21561-cempre-2016-empresas-e-outras-organizacoes-perderam-2-1-milhoes-de-ocupados-entre-2015-e-2016.html 9016 9016|Estatísticas do Cadastro Central de Empresas - CEMPRE|estatisticas-do-cadastro-central-de-empresas|2000 9016 Release CEMPRE 2016: empresas e outras organizações perderam 2,1 milhões de ocupados entre 2015 e 2016 20241013_085511 101 - to - 110 - 20241012_093551 27/06/2018 10:00:00 true economicas 21562 {"image_intro":"images\/agenciadenoticias\/estatisticas_economicas\/2018_06\/cempre_thumb.jpg","float_intro":"","image_intro_alt":"#PraCegoVer Vista frontal de pr\u00e9dios comerciais","image_intro_caption":"","image_fulltext":"images\/agenciadenoticias\/estatisticas_economicas\/2018_06\/cempre_home.jpg","float_fulltext":"","image_fulltext_alt":"#PraCegoVer Vista frontal de pr\u00e9dios comerciais","image_fulltext_caption":""} A população assalariada com diploma cresceu 1,6% em 2016 - Foto: Licia Rubinstein/Agência IBGE Notícias As empresas e outras organizações perderam 2,1 milhões de profissionais assalariados em 2016, uma queda de 4% em relação ao ano anterior, e a segunda... http://agenciadenoticias.ibge.gov.br/agencia-noticias/2012-agencia-de-noticias/noticias/21562-ocupacao-formal-cai-mas-proporcao-de-assalariados-com-diploma-cresce-em-2016.html 9016 9016|Estatísticas do Cadastro Central de Empresas - CEMPRE|estatisticas-do-cadastro-central-de-empresas|2000 9016 Notícia Ocupação formal cai, mas proporção de assalariados com diploma cresce em 2016 20241013_085511 101 - to - 110 - 20241012_093551 26/06/2018 10:00:00 true ibge 21556 {"image_intro":"images\/agenciadenoticias\/ibge\/2018_06\/acordo_thumb.jpg","float_intro":"","image_intro_alt":"#praCegoVer Roberto Olinto Ramos, presidente do IBGE, e Julio Santaella mostram acordo de coopera\u00e7\u00e3o t\u00e9cnica","image_intro_caption":"","image_fulltext":"images\/agenciadenoticias\/ibge\/2018_06\/acordo_home.jpg","float_fulltext":"","image_fulltext_alt":"#praCegoVer Roberto Olinto Ramos, presidente do IBGE, e Julio Santaella mostram acordo de coopera\u00e7\u00e3o t\u00e9cnica","image_fulltext_caption":""} Representado pelo presidente Roberto Olinto, o IBGE assinou, na última semana, acordos de cooperação técnica com os institutos de estatística do México (INEGI) e da União Europeia (Eurostat). A formalização dos pactos foi feita entre a 66ª Sessão... http://agenciadenoticias.ibge.gov.br/agencia-noticias/2012-agencia-de-noticias/noticias/21556-ibge-assina-acordos-de-cooperacao-com-mexico-e-uniao-europeia.html 0 Notícia IBGE assina acordos de cooperação com México e União Europeia 20241013_085511 101 - to - 110 - 20241012_093551 25/06/2018 10:00:00 true ibge 21545 {"image_intro":"images\/agenciadenoticias\/ibge\/2018_06\/comissao1_thumb.jpg","float_intro":"","image_intro_alt":"#PraCegoVer Participantes da Comiss\u00e3o Consultiva do Censo 2020","image_intro_caption":"","image_fulltext":"images\/agenciadenoticias\/ibge\/2018_06\/comissao1_home_2.jpg","float_fulltext":"","image_fulltext_alt":"#PraCegoVer Participantes da Comiss\u00e3o Consultiva do Censo 2020","image_fulltext_caption":""} A primeira r

In [0]:
# display(dbutils.fs.ls('dbfs:/mnt/bronze/'))

## apagar pastas
# dbutils.fs.rm('dbfs:/mnt/raw/',True)
# dbutils.fs.rm('dbfs:/mnt/bronze/',True)
# dbutils.fs.rm('dbfs:/mnt/historic/bronze/',True)

## criar pasta
# dbutils.fs.mkdirs('dbfs:/mnt/raw/')
# dbutils.fs.mkdirs('dbfs:/mnt/raw_2/')
# dbutils.fs.mkdirs('dbfs:/mnt/raw_3/')

In [0]:
# ### é Possivel fazer a Leitura de varios arquivos de forma Multipla, passando a referencia deles dentro de uma lista  ##########

# spark.read.json(files).display()